In [0]:
from pyspark.sql import SparkSession
from pyspark.sql import types as t
from pyspark.sql import functions as f
from pyspark.sql.window import Window as w
from datetime import datetime, timedelta

## Mount S3 Bucket to DBFS

In [0]:
ACCESS_KEY = "<s3-access-key>"
SECRET_KEY = "<s3-secret-key>"
BUCKET_NAME = "lab10"
MOUNT_NAME = "<dbfs-mount-name>"


dbutils.fs.mount(f"s3a://{ACCESS_KEY}:{SECRET_KEY}@{BUCKET_NAME}", f"/mnt/{MOUNT_NAME}")

Out[2]: True

In [0]:
display(dbutils.fs.ls(f"/mnt/{MOUNT_NAME}"))

path name size modificationTime dbfs:/mnt/qep_welldata_test_s3/GB_category_id.json GB_category_id.json 8225 1654458135000 dbfs:/mnt/qep_welldata_test_s3/GBvideos.csv GBvideos.csv 53213441 1654452501000

## Prepare Datasets

In [0]:
categories_df = spark.read.format("json") \
    .option("multiline","true") \
    .load(f"/mnt/{MOUNT_NAME}/GB_category_id.json")

categories_df = (
    categories_df
        .withColumn("categories_exploaded", f.explode(f.arrays_zip("items.id", "items.snippet.title")))
        .select(
            f.col("categories_exploaded.id").alias("id"),
            f.col("categories_exploaded.title").alias("title"),
        )
)

In [0]:
display(categories_df)

id title 1 Film & Animation 2 Autos & Vehicles 10 Music 15 Pets & Animals 17 Sports 18 Short Movies 19 Travel & Events 20 Gaming 21 Videoblogging 22 People & Blogs 23 Comedy 24 Entertainment 25 News & Politics 26 Howto & Style 27 Education 28 Science & Technology 30 Movies 31 Anime/Animation 32 Action/Adventure 33 Classics 34 Comedy 35 Documentary 36 Drama 37 Family 38 Foreign 39 Horror 40 Sci-Fi/Fantasy 41 Thriller 42 Shorts 43 Shows 44 Trailers

In [0]:
videos_df = spark.read.format("csv") \
    .option("header", True) \
    .option("sep", ",") \
    .option("multiline", True) \
    .load(f"/mnt/{MOUNT_NAME}/GBvideos.csv")

In [0]:
display(videos_df)

video_id trending_date title channel_title category_id publish_time tags views likes dislikes comment_count thumbnail_link comments_disabled ratings_disabled video_error_or_removed description Jw1Y-zhQURU 17.14.11 John Lewis Christmas Ad 2017 - #MozTheMonster John Lewis 26 2017-11-10T07:38:29.000Z "christmas"|"john lewis christmas"|"john lewis"|"christmas ad"|"mozthemonster"|"christmas 2017"|"christmas ad 2017"|"john lewis christmas advert"|"moz" 7224515 55681 10247 9479 https://i.ytimg.com/vi/Jw1Y-zhQURU/default.jpg False False False Click here to continue the story and make your own monster:\nhttp://bit.ly/2mboXgj\n\nJoe befriends a noisy Monster under his bed but the two have so much fun together that he can't get to sleep, leaving him tired by day. For Christmas Joe receives a gift to help him finally get a good night’s sleep.\n\nShop the ad\nhttp://bit.ly/2hg04Lc\n\nThe music is Golden Slumbers performed by elbow, the original song was by The Beatles. \nFind the track:\nhttps://Elbow.lnk.to/GoldenSlumbersXS\n\nSubscribe to this channel for regular video updates\nhttp://bit.ly/2eU8MvW\n\nIf you want to hear more from John Lewis:\n\nLike John Lewis on Facebook\nhttp://www.facebook.com/johnlewisretail\n\nFollow John Lewis on Twitter\nhttp://twitter.com/johnlewisretail\n\nFollow John Lewis on Instagram\nhttp://instagram.com/johnlewisretail 3s1rvMFUweQ 17.14.11 Taylor Swift: …Ready for It? (Live) - SNL Saturday Night Live 24 2017-11-12T06:24:44.000Z "SNL"|"Saturday Night Live"|"SNL Season 43"|"Episode 1730"|"Tiffany Haddish"|"Taylor Swift"|"Taylor Swift Ready for It"|"s43"|"s43e5"|"episode 5"|"live"|"new york"|"comedy"|"sketch"|"funny"|"hilarious"|"late night"|"host"|"music"|"guest"|"laugh"|"impersonation"|"actor"|"improv"|"musician"|"comedian"|"actress"|"If Loving You Is Wrong"|"Oprah Winfrey"|"OWN"|"Girls Trip"|"The Carmichael Show"|"Keanu"|"Reputation"|"Look What You Made Me Do"|"ready for it?" 1053632 25561 2294 2757 https://i.ytimg.com/vi/3s1rvMFUweQ/default.jpg False False False Musical guest Taylor Swift performs …Ready for It? on Saturday Night Live.\n\n#SNL #SNL43\n\nGet more SNL: http://www.nbc.com/saturday-night-live\nFull Episodes: http://www.nbc.com/saturday-night-liv...\n\nLike SNL: https://www.facebook.com/snl\nFollow SNL: https://twitter.com/nbcsnl\nSNL Tumblr: http://nbcsnl.tumblr.com/\nSNL Instagram: http://instagram.com/nbcsnl \nSNL Pinterest: http://www.pinterest.com/nbcsnl/ n1WpP7iowLc 17.14.11 Eminem - Walk On Water (Audio) ft. Beyoncé EminemVEVO 10 2017-11-10T17:00:03.000Z "Eminem"|"Walk"|"On"|"Water"|"Aftermath/Shady/Interscope"|"Rap" 17158579 787420 43420 125882 https://i.ytimg.com/vi/n1WpP7iowLc/default.jpg False False False Eminem's new track Walk on Water ft. Beyoncé is available everywhere: http://shady.sr/WOWEminem \nPlaylist Best of Eminem: https://goo.gl/AquNpo\nSubscribe for more: https://goo.gl/DxCrDV\n\nFor more visit: \nhttp://eminem.com\nhttp://facebook.com/eminem\nhttp://twitter.com/eminem\nhttp://instagram.com/eminem\nhttp://eminem.tumblr.com\nhttp://shadyrecords.com\nhttp://facebook.com/shadyrecords\nhttp://twitter.com/shadyrecords\nhttp://instagram.com/shadyrecords\nhttp://trustshady.tumblr.com\n\nMusic video by Eminem performing Walk On Water. (C) 2017 Aftermath Records\nhttp://vevo.ly/gA7xKt PUTEiSjKwJU 17.14.11 Goals from Salford City vs Class of 92 and Friends at The Peninsula Stadium! Salford City Football Club 17 2017-11-13T02:30:38.000Z "Salford City FC"|"Salford City"|"Salford"|"Class of 92"|"University of Salford"|"Salford Uni"|"Non League"|"National League"|"National League North" 27833 193 12 37 https://i.ytimg.com/vi/PUTEiSjKwJU/default.jpg False False False Salford drew 4-4 against the Class of 92 and Friends at the newly opened The Peninsula Stadium!\n\nLike us on Facebook: https://www.facebook.com/SalfordCityFC/ \nFollow us on Twitter: https://twitter.com/SalfordCityFC\nFollow us on Instagram: https://www.instagram.com/salfordcityfc/ \nSubscribe to us on YouTube: https://

## Task #1

In [0]:
def top_trending_videos(videos_df, limit=0):
    """
    Find Top 10 videos that were amongst the trending videos for the highest number of days 
    (it doesn't need to be a consecutive period of time). You should also include information 
    about different metrics for each day the video was trending.
    """
    # Cast and transform input data.
    df = videos_df.select(
        f.col("video_id").alias("id"),
        f.col("title"),
        f.col("description"),
        f.struct(
            f.to_date(f.from_unixtime(f.unix_timestamp(f.col("trending_date"), "yy.dd.MM"))).alias("date"), 
            f.col("views").cast(t.LongType()).alias("views"), 
            f.col("likes").cast(t.LongType()).alias("likes"), 
            f.col("dislikes").cast(t.LongType()).alias("dislikes")
        ).alias("trendingDay")
    )

    # Get a total number of days in trending for each video.
    total_trending_df = df \
        .groupBy(f.col("id")).agg(f.count(f.col("trendingDay.date")).alias("totalTrendingDays")) \
        .select(f.col("id"), f.col("totalTrendingDays"))

    # Rank the latest day of video being in trends as 1.
    # Get the latest views, likes and dislikes. 
    window = w.partitionBy("id").orderBy(f.col("trendingDay.date").desc())
    latest_stats_df = df \
        .withColumn("rank", f.row_number().over(window)) \
        .where(f.col("rank") == 1) \
        .select(
            f.col("id"), 
            f.col("trendingDay.views").alias("latestViews"), 
            f.col("trendingDay.likes").alias("latestLikes"), 
            f.col("trendingDay.dislikes").alias("latestDislikes")
        )

    # Collect all trendingDay statistics into a single array for each video.
    premerge_df = df \
        .groupBy("id", "title", "description").agg(f.collect_list(f.col("trendingDay")).alias("trendingDays")) \

    # Get top 10 videos by number of days in trending.
    merge_df = (
        premerge_df
            .join(total_trending_df, ["id"], how="left")
            .join(latest_stats_df, ["id"], how="left")
            .select(
                f.col("id"),
                f.col("title"),
                f.col("description"),
                f.col("latestViews"),
                f.col("latestLikes"),
                f.col("latestDislikes"),
                f.col("trendingDays"),
                f.col("totalTrendingDays")
            )
    )
    merge_df.count()

    # Collect all videos in an array.
    collected_df = merge_df.select(
        f.struct(
            f.col("id"),
            f.col("title"),
            f.col("description"),
            f.col("latestViews"),
            f.col("latestLikes"),
            f.col("latestDislikes"),
            f.col("trendingDays")
        ).alias("video")
    )
    
    if limit > 0:
        return collected_df.orderBy(f.col("totalTrendingDays").desc()).limit(limit)
    return collected_df    

In [0]:
top_trending_videos_df = top_trending_videos(videos_df, limit=10)
display(top_trending_videos_df)

video List(NooW_RbfdWI, Jurassic World: Fallen Kingdom - Official Trailer #2 [HD], Jurassic World: Fallen Kingdom \nIn Theaters June 22, 2018 \nTry the Jurassic World effect on your Facebook camera: http://unvrs.al/JWFBCam \n\nhttps://www.jurassicworld.com \n\nIt’s been four years since theme park and luxury resort Jurassic World was destroyed by dinosaurs out of containment. Isla Nublar now sits abandoned by humans while the surviving dinosaurs fend for themselves in the jungles. \n\nWhen the island’s dormant volcano begins roaring to life, Owen (Chris Pratt) and Claire (Bryce Dallas Howard) mount a campaign to rescue the remaining dinosaurs from this extinction-level event. Owen is driven to find Blue, his lead raptor who’s still missing in the wild, and Claire has grown a respect for these creatures she now makes her mission. Arriving on the unstable island as lava begins raining down, their expedition uncovers a conspiracy that could return our entire planet to a perilous order not seen since prehistoric times.\n\nWith all of the wonder, adventure and thrills synonymous with one of the most popular and successful series in cinema history, this all-new motion-picture event sees the return of favorite characters and dinosaurs—along with new breeds more awe-inspiring and terrifying than ever before. Welcome to Jurassic World: Fallen Kingdom. \n\nStars Pratt and Howard return alongside executive producers Steven Spielberg and Colin Trevorrow for Jurassic World: Fallen Kingdom. They are joined by co-stars James Cromwell, Ted Levine, Justice Smith, Geraldine Chaplin, Daniella Pineda, Toby Jones, Rafe Spall and Isabella Sermon, while BD Wong and Jeff Goldblum reprise their roles. \n\nDirected by J.A. Bayona (The Impossible), the epic action-adventure is written by Jurassic World’s director, Trevorrow, and its co-writer, Derek Connolly. Producers Frank Marshall and Pat Crowley once again partner with Spielberg and Trevorrow in leading the filmmakers for this stunning installment. Belén Atienza joins the team as a producer., 24293173, 275268, 7806, List(List(2018-02-05, 1999326, 61833, 1416), List(2018-02-06, 8293323, 162435, 4232), List(2018-02-07, 11883172, 200007, 5377), List(2018-02-08, 14297585, 219417, 5899), List(2018-02-09, 16344681, 232342, 6276), List(2018-02-10, 18087776, 240891, 6542), List(2018-02-11, 19617103, 246215, 6745), List(2018-02-12, 20291688, 249906, 6906), List(2018-02-13, 20605167, 252139, 7002), List(2018-02-14, 21113889, 254342, 7076), List(2018-02-15, 21532935, 256613, 7165), List(2018-02-16, 21766666, 257599, 7214), List(2018-02-17, 22031279, 259059, 7252), List(2018-02-18, 22329175, 261085, 7310), List(2018-02-19, 22593205, 263095, 7359), List(2018-02-20, 22762324, 264419, 7407), List(2018-02-21, 22892962, 265445, 7436), List(2018-02-22, 23004406, 266286, 7464), List(2018-02-23, 23133164, 267163, 7509), List(2018-02-24, 23248398, 267919, 7554), List(2018-02-25, 23375947, 268748, 7578), List(2018-02-26, 23476709, 269416, 7600), List(2018-02-27, 23541453, 269823, 7616), List(2018-02-28, 23597260, 270189, 7630), List(2018-03-01, 23658987, 270651, 7642), List(2018-03-02, 23705031, 270974, 7651), List(2018-03-03, 23759046, 271406, 7662), List(2018-03-04, 23823732, 271842, 7681), List(2018-03-05, 23886937, 272351, 7692), List(2018-03-06, 23920721, 272586, 7697), List(2018-03-07, 23959627, 272840, 7705), List(2018-03-08, 23998220, 273106, 7718), List(2018-03-09, 24043823, 273428, 7732), List(2018-03-10, 24096967, 273829, 7748), List(2018-03-11, 24161883, 274303, 7766), List(2018-03-12, 24214227, 274680, 7782), List(2018-03-13, 24249582, 274993, 7792), List(2018-03-14, 24293173, 275268, 7806))) List(2z3EUY1aXdY, Justin Timberlake’s FULL Pepsi Super Bowl LII Halftime Show! | NFL Highlights, Justin Timberlake breaks it down during the Pepsi Super Bowl LII Halftime Show. The Philadelphia Eagles take on the New England Patriots during Super Bowl LII.\n\nWatch full games with NFL Game Pass: https://www.nfl.com/game

## Task #2

In [0]:
week_boundaries_schema = t.StructType([
    t.StructField("start_date", t.DateType()),
    t.StructField("end_date", t.DateType())
])


@f.udf(week_boundaries_schema)
def get_week_boundaries(date):
    date_dt = datetime.strptime(str(date), "%Y-%m-%d")
    start = date_dt - timedelta(days=date_dt.weekday())
    end = start + timedelta(days=6)
    return start, end

In [0]:
def top_week_categories(videos_df, categories_df):
    """
    Find what was the most popular category for each week (7 days slices). 
    Popularity is decided based on the total number of views for videos of
    this category. Note, to calculate it you can’t just sum up the number of views. 
    If a particular video appeared only once during the given period, it shouldn’t 
    be counted. Only if it appeared more than once you should count the number of new 
    views. For example, if video A appeared on day 1 with 100 views, then on day 4 with 
    250 views and again on day 6 with 400 views, you should count it as 400.
    For our purpose, it will mean that this particular video was watched 300 times in 
    the given time period.
    """
    # Cast and transform input data.
    weeks_df = videos_df \
    .select(
        f.col("video_id").alias("id"),
        f.to_date(f.from_unixtime(f.unix_timestamp(f.col("trending_date"), "yy.dd.MM"))).alias("date"), 
        f.col("views").cast(t.LongType()).alias("views"), 
        f.col("category_id"),
    )
    
    # Get week start and end dates.
    weeks_df = weeks_df \
        .withColumn("week_boundaries", get_week_boundaries(f.col("date"))) \
        .select(
            f.col("id"),
            f.col("views"),
            f.col("date"),
            f.col("category_id"),
            f.col("week_boundaries.start_date").alias("start_date"),
            f.col("week_boundaries.end_date").alias("end_date")
    )
    
    # Get all videos that occur more than once a week. 
    # Calculate the amount of new views for each video every week.
    video_views_weekly_df = (
        weeks_df
            .groupBy("start_date", "end_date", "id", "category_id")
            .agg(
                f.count("id").alias("count"), 
                f.collect_list(f.col("views")).alias("views_list")
            )
            .where(f.col("count") >= 2).
            select(
                f.col("id"),
                f.col("start_date"),
                f.col("end_date"),
                f.col("category_id"),
                (f.array_max(f.col("views_list")) - f.array_min(f.col("views_list"))).alias("views_delta")
            )
    )
    
    # Get a single top category and its statistics for each week.
    window = w.partitionBy("start_date", "end_date").orderBy(f.col("total_views").desc())
    week_top_categories_df = (
        video_views_weekly_df
            .groupBy("start_date", "end_date", "category_id")
            .agg(
                f.count("id").alias("number_of_videos"), 
                f.sum(f.col("views_delta")).alias("total_views"),
                f.collect_list(f.col("id")).alias("video_ids")
            )
            .withColumn("rank", f.row_number().over(window))
            .where(f.col("rank") == 1)
    )
    
    # Join with categories DF to get category title.
    # Collect all weeks in an array.
    week_top_categories_df = (
    week_top_categories_df.alias("wtc")
        .join(categories_df.alias("ce"), f.col("wtc.category_id") == f.col("ce.id"), how="left")
        .select(
            f.struct(
                f.col("wtc.start_date"),
                f.col("wtc.end_date"),
                f.col("wtc.category_id"),
                f.col("ce.title").alias("category_name"),
                f.col("wtc.number_of_videos"),
                f.col("wtc.total_views"),
                f.col("wtc.video_ids")
            ).alias("weeks")
        )
    )
    return week_top_categories_df

In [0]:
week_top_categories_df = top_week_categories(videos_df, categories_df)
display(week_top_categories_df)

weeks List(2017-11-13, 2017-11-19, 10, Music, 70, 115915504, List(-crLmRLgeNE, 2Vv-BfVoq4g, 2Zvmi5BzDbs, 44NYFvhXmW8, 4GFAZBKZVJY, 4SANXNco_y4, 4j-ED6tL85o, 54Eae2ewc1c, 5E4ZBSInqUU, 6uJf2IT2Zh8, 7JMV6iBlXFo, 7fm7mll2qvg, 8HON4AswPVk, 8l_e6bx8UG8, 949vJMp0v40, 9t9u_yPEidY, 9wg3v-01yKQ, CyzEtbG-sxY, DIU3xPdhCBI, E7q_wbbwGyU, ENr6CXm1YxU, FUzs2oMEs8w, HJBqbRMUOaI, HNa_UWX51_s, Hw2e2XS9Wmc, IOd0HGH6xKI, J_QGZspO4gg, LMCuKltaY3M, L_u97PqWX6g, MKLlDnUqho4, NHglTopVlKQ, NVCqz2BDfcQ, Nsw5HuVGdBI, OGKchfcd-5w, PHWAZNkqwN4, Q-KsToawMJE, QFfEtKvXMAs, QOksZ8VogRw, RrhSJzM8NLE, TQ2uDO5CbYg, TbfxmTQkLAE, U0yo2XqufgU, UuCq8mtK8J4, V54CEElTF_U, VEoOuF_cN0Q, W187SzNVGvc, Wjq7x2d_s1w, X9VlCV1ZflQ, aRz_XfwcVtU, au3S8F08v54, bRlXatOvsZU, eHIY3HNNqzM, eQVhAN7-IAw, iNf6VErGDLI, ixxR3ZoqnF0, jG1JY0rt2Os, kGOmPmILndU, lYN26wt1lJQ, lo5ERI5nPbM, n1WpP7iowLc, nVzA1uWTydQ, ozkqm2ifMw8, pHE8nIB6j2U, pOEzjT-SED0, pz95u3UVpaM, r1afdZk0qcI, rnhlTS8RgUM, svZScJMh4Pg, xg9ebVTL9yE, xzpQSINtLkw)) List(2017-11-20, 2017-11-26, 10, Music, 69, 154127373, List(1ihTE5cxUCQ, 2Vv-BfVoq4g, 2Zvmi5BzDbs, 3BEpWWxPXSU, 44NYFvhXmW8, 4SANXNco_y4, 54Eae2ewc1c, 5E4ZBSInqUU, 6uJf2IT2Zh8, 7fm7mll2qvg, 949vJMp0v40, 9t9u_yPEidY, 9wg3v-01yKQ, BQ_0QLL2gqI, DIU3xPdhCBI, DpSWgZVIfi8, EBt_88nxG4c, ENr6CXm1YxU, FUzs2oMEs8w, FaJmopuuhZE, GO4hi9004hg, HJBqbRMUOaI, HNa_UWX51_s, IOd0HGH6xKI, J_QGZspO4gg, K6xwB8Kkce0, LMCuKltaY3M, M6LTqtYKDtI, MKLlDnUqho4, NVCqz2BDfcQ, Nsw5HuVGdBI, OGKchfcd-5w, PHWAZNkqwN4, QFfEtKvXMAs, QOksZ8VogRw, RP3UsFrDJfY, RrhSJzM8NLE, UQHSK-kgONk, UceaB4D0jpo, UuCq8mtK8J4, Uz-uEW_Rur4, V3EYjVPRClU, VEoOuF_cN0Q, VYzDZ1qeKEc, W187SzNVGvc, WXlr35jV3cw, Yhea380bYp0, cmc8q2dcIMs, eHIY3HNNqzM, eQVhAN7-IAw, ec9r9THD5eU, ixxR3ZoqnF0, jG1JY0rt2Os, jH2t4Tcl3Pg, jjwiwepvS1o, jpl2X8tDfIA, kTlv5_Bs8aw, lMSHTnkVJVs, n1WpP7iowLc, nUv22OHdjQU, oddXT5uaRb8, pHE8nIB6j2U, pOEzjT-SED0, pz95u3UVpaM, svZScJMh4Pg, tz23WFb8HM0, w1fN1_9BNM8, xg9ebVTL9yE, xzpQSINtLkw)) List(2017-11-27, 2017-12-03, 10, Music, 69, 113428687, List(1ihTE5cxUCQ, 2BE4X3bYpxY, 2kfIkm5qVsQ, 2nJ3U5dzvPs, 3BEpWWxPXSU, 44W9qstI8H8, 4SANXNco_y4, 4xN-jUfJAyM, 5E4ZBSInqUU, 6uJf2IT2Zh8, 7AXo-bYGXI4, 817P8W8-mGE, BQ_0QLL2gqI, DpSWgZVIfi8, EBt_88nxG4c, FaJmopuuhZE, Fjm81OPZbpU, GO4hi9004hg, HJBqbRMUOaI, JcC5VGOx8I8, K6xwB8Kkce0, LgmxMuW6Fsc, M6LTqtYKDtI, NRh8KWiCxWU, Nsw5HuVGdBI, PHWAZNkqwN4, RP3UsFrDJfY, RrhSJzM8NLE, SA7AIQw-7Ms, UQHSK-kgONk, UceaB4D0jpo, UqItlHUSN-4, UuCq8mtK8J4, Uz-uEW_Rur4, V3EYjVPRClU, VTVLcK2zybM, VYzDZ1qeKEc, WLagbArQsuE, WXlr35jV3cw, Yhea380bYp0, YsXK7vGLoTA, Z35ALmnFo9A, c5_LROaHGtw, cmc8q2dcIMs, d8GHT9nK66Y, e7b5hbWvWEQ, eQVhAN7-IAw, ec9r9THD5eU, jG1JY0rt2Os, jH2t4Tcl3Pg, jjwiwepvS1o, jpl2X8tDfIA, k9oMv0JzCn8, kTlv5_Bs8aw, lMSHTnkVJVs, nSuregWhlWk, nUv22OHdjQU, nXDZCuFESSU, nx1R-eHSkfM, o7iL2KzDh38, o9zRQijCN5w, pOEzjT-SED0, qgGooEyeNNc, qu-biRtYEcU, r5g85U5lJso, svZScJMh4Pg, tz23WFb8HM0, w1fN1_9BNM8, xSmgnf6PHmE)) List(2017-12-04, 2017-12-10, 24, Entertainment, 62, 115087023, List(09lz1fRBBsY, 0EQuVfP-vXs, 0hcp-eMOn4E, 15aTCG3as6Q, 1l26UFQ06eQ, 1sl5KJ69qiA, 3XklsSF53pc, 5ELQ6u_5YYM, 6ZfuNTqbHE8, 8kFnLQySIzU, 8mFUhpKz01s, 9Ktmmjt8Tq4, AM1pavPRU8E, BnANUza_uXQ, EAuQBaienc8, FlsCjmMhFmw, I6N-XuYllgA, IbVR4kzVQrk, Ic8yK9YLyak, JJWOLBw7tEY, KtqVezaUhkA, Kx-TGqqMuPU, LPBPma9YJnE, LctCTZKdO18, OHOkdEBpwDc, PPCDMi5xmmk, Rm09nLK-Pg8, SNCMtOdaIxU, TbniWvd5OZ4, UXm1xHECZu0, W8_T7MMywcs, XZNUgzO9xJA, Yedbkvwm2rY, Yjf5scyjifU, Yp5R84V1bDU, ZsT3m5jdjr8, aJ9XruZm_Hg, bOBL980Xsg4, bvBNvAMeovw, cHB_s970Uyw, dsNNfiA6qjs, e5IRkF20JmU, f3uZxD39awA, ggpoZyF2lU0, hNsd-m30m2E, hzCeq0-Vd1U, jLM2ibaRbrk, k_aT3jAK_QU, kmH6rve3qF0, me5ifeBFaFo, nVHcXZK7pKs, nVrkQyLS4oE, os5mMTl3IBs, pDi7cezk9CA, qLVZiKDNxtw, rCnU-IDcnnI, vW7H-DKivX8, vn9mMeWcgoM, y8dm1IbpMj4, yef_HfQoBd8, yqFIrrcmsJI, zB1pY4n_FyQ)) List(2017-12-11, 2017-12-17, 10, Music, 82, 101625935, List(2kfIkm5qVsQ, 44W9qstI8H8, 48qcnpCWBq0, 4W_YgNW7gs0, 4cucHc2vef4, 4xN-jUfJAyM, 56KYMMGudcU, 5ZoKBdxhXpw, 5fW5dsc0-5g, 60Qi7Zv6Wbg, 66kn6Dcr12E, 7AXo-bYGXI4, 7Q5dDVHGr1M, 817

## Task #3

In [0]:
date_ranges_schema = t.ArrayType(
    t.StructType([
        t.StructField("start_date", t.DateType()),
        t.StructField("end_date", t.DateType())
    ])
)


@f.udf(date_ranges_schema)
def date_ranges_udf(date):
    delta = timedelta(days=30)
    
    dates = []
    
    min_start_date = date - delta
    max_end_date = date + delta
    
    start_date = min_start_date
    end_date = date
    while end_date != max_end_date:
        dates.append([start_date, end_date])
        
        start_date += timedelta(days=1)
        end_date += timedelta(days=1)
    
    return dates

In [0]:
def top_tags_monthly(videos_df):
    """
    What were the 10 most used tags amongst trending videos for each 30days time period? 
    Note, if during the specified period the same video appears multiple times,
    you should count tags related to that video only once.
    """
    # Split tags by | and explode them into separate rows.
    # Get rid from tags that appear twice.
    tags_exploaded_df = (
        videos_df
            .select(
                f.col("video_id"),
                f.split(f.regexp_replace(f.col("tags"), '\"', ''), "\|").alias("tags_array"),
                f.to_date(f.from_unixtime(f.unix_timestamp(f.col("trending_date"), "yy.dd.MM"))).alias("date")
            )
            .withColumn("tag", f.explode(f.col("tags_array")))
            .select(
                f.col("video_id"),
                f.col("tag"),
                f.col("date")
            ).distinct()
    )
    
    # Calculate the date ranges for each record. (date - 30 days; date + 30 days)
    # Explode those ranges.
    tags_time_periods_df = (
        tags_exploaded_df
            .withColumn("start_end_dates", date_ranges_udf(f.col("date")))
            .withColumn("ranges", f.explode(f.col("start_end_dates")))
            .select(
                f.col("video_id"),
                f.col("tag"),
                f.col("date"),
                f.col("ranges.start_date").alias("start_date"),
                f.col("ranges.end_date").alias("end_date")
            )      
    )
    
    # Get top 10 tags for each date range.
    window =  w.partitionBy("start_date", "end_date").orderBy(f.col("number_of_videos").desc())
    top_tags_ranged_df = (
        tags_time_periods_df
            .groupBy("tag", "start_date", "end_date")
            .agg(
                f.count(f.col("video_id")).alias("number_of_videos"), 
                f.collect_list(f.col("video_id")).alias("video_ids")
            )
            .withColumn("rank", f.row_number().over(window))
            .where(f.col("rank") <= 10)
            .select(
                f.col("start_date"),
                f.col("end_date"),
                f.struct(
                    f.col("tag"),
                    f.col("number_of_videos"),
                    f.col("video_ids")
                ).alias("tag_stat")
            )
    )
    
    # Transform data to the final form.
    top_used_tags_df = (
        top_tags_ranged_df.
            groupBy("start_date", "end_date")
            .agg(f.collect_list(f.col("tag_stat")).alias("tags"))
            .select(f.struct(
                f.col("start_date"),
                f.col("end_date"),
                f.col("tags")
            ).alias("month"))
    )
    return top_used_tags_df

In [0]:
top_tags_monthly_df = top_tags_monthly(videos_df)
display(top_tags_monthly_df)

month List(2017-10-29, 2017-11-28, List(List(funny, 227, List(YInRqgNMLBc, 5nEogChRGE8, DJXUWLs6FI0, p8XP7A7kvzM, iDXlWTRyxgE, 3s1rvMFUweQ, 3iXwXYflCSI, hpapqEeb36k, nlodY8nMw-A, 5nEogChRGE8, cHB_s970Uyw, j7WlcSwe8Ws, 510KQ_LXGww, Mv-CJ44KbW4, sECcOTO8Ij4, nlodY8nMw-A, YInRqgNMLBc, nlodY8nMw-A, VsYmwBOYfW8, p8XP7A7kvzM, 3iXwXYflCSI, F6rBIWN8SsM, hpapqEeb36k, 3iXwXYflCSI, XymR5UCxSfA, leFNoUJmJ9o, wsXxfgJZ4E4, 510KQ_LXGww, F6rBIWN8SsM, Mv-CJ44KbW4, 5nEogChRGE8, 510KQ_LXGww, Mv-CJ44KbW4, 0PW9MWDWLH8, nlodY8nMw-A, 6p-QzY5bxJ0, 0oXu0XfXYYE, Z1rZAT2GtmI, DJXUWLs6FI0, Da2crn5NXc4, cHB_s970Uyw, hpapqEeb36k, leFNoUJmJ9o, cHB_s970Uyw, aKPz583WRpQ, tpyQLIpv4Yk, nlodY8nMw-A, mwpHSMv1pI4, 3iXwXYflCSI, 510KQ_LXGww, 5nEogChRGE8, oSS6kGWNEeA, p8XP7A7kvzM, YInRqgNMLBc, I2kAkhboAn8, p8XP7A7kvzM, 5nEogChRGE8, FHl0nIdbiLA, _H1vcldAsP0, FHl0nIdbiLA, Mv-CJ44KbW4, 3s1rvMFUweQ, Mv-CJ44KbW4, Z1rZAT2GtmI, DJXUWLs6FI0, MjdpR-TY6QU, MjdpR-TY6QU, jDvKFN6aYsE, 0PW9MWDWLH8, sECcOTO8Ij4, j7WlcSwe8Ws, YInRqgNMLBc, sECcOTO8Ij4, p8XP7A7kvzM, sECcOTO8Ij4, sECcOTO8Ij4, nlodY8nMw-A, wsXxfgJZ4E4, sottGW1p5os, sECcOTO8Ij4, wsXxfgJZ4E4, FHl0nIdbiLA, 5nEogChRGE8, hpapqEeb36k, _H1vcldAsP0, hpapqEeb36k, FHl0nIdbiLA, nlodY8nMw-A, Z1rZAT2GtmI, 3jtjkXSvuJw, Da2crn5NXc4, sECcOTO8Ij4, Mv-CJ44KbW4, 5nEogChRGE8, aKPz583WRpQ, leFNoUJmJ9o, SCnVbXlC1Ds, 3jtjkXSvuJw, dHDn26UX4aw, Da2crn5NXc4, Z1rZAT2GtmI, VsYmwBOYfW8, mwpHSMv1pI4, 5nEogChRGE8, cJ1zhq3yNBM, cHB_s970Uyw, hpapqEeb36k, 510KQ_LXGww, 5nEogChRGE8, hpapqEeb36k, oSS6kGWNEeA, cHB_s970Uyw, aKPz583WRpQ, p8XP7A7kvzM, 5nEogChRGE8, DJXUWLs6FI0, wsXxfgJZ4E4, p8XP7A7kvzM, jDvKFN6aYsE, F6rBIWN8SsM, nlodY8nMw-A, 3s1rvMFUweQ, 7DLKv39MLbg, F6rBIWN8SsM, puREqwXzyCI, hpapqEeb36k, 3jtjkXSvuJw, DJXUWLs6FI0, mwpHSMv1pI4, Mv-CJ44KbW4, YInRqgNMLBc, hpapqEeb36k, 5nEogChRGE8, mwpHSMv1pI4, YInRqgNMLBc, Da2crn5NXc4, cHB_s970Uyw, FHl0nIdbiLA, Mv-CJ44KbW4, 3jtjkXSvuJw, p8XP7A7kvzM, Da2crn5NXc4, 0PW9MWDWLH8, AumaWl0TNBo, VsYmwBOYfW8, Mv-CJ44KbW4, Mv-CJ44KbW4, leFNoUJmJ9o, dgW5kpeSB1A, F6rBIWN8SsM, mwpHSMv1pI4, nlodY8nMw-A, hpapqEeb36k, _H1vcldAsP0, F6rBIWN8SsM, hSXf6ozQEwo, leFNoUJmJ9o, wsXxfgJZ4E4, 3iXwXYflCSI, jDvKFN6aYsE, YInRqgNMLBc, 0PW9MWDWLH8, 0PW9MWDWLH8, _H1vcldAsP0, wsXxfgJZ4E4, puREqwXzyCI, p8XP7A7kvzM, oSS6kGWNEeA, puREqwXzyCI, XymR5UCxSfA, nlodY8nMw-A, F6rBIWN8SsM, puREqwXzyCI, Mv-CJ44KbW4, 6p-QzY5bxJ0, 3jtjkXSvuJw, mwpHSMv1pI4, mwpHSMv1pI4, cJ1zhq3yNBM, Da2crn5NXc4, _H1vcldAsP0, MjdpR-TY6QU, YInRqgNMLBc, FHl0nIdbiLA, 5nEogChRGE8, 3jtjkXSvuJw, 5nEogChRGE8, 3iXwXYflCSI, sECcOTO8Ij4, -XjayddbksQ, nlodY8nMw-A, 510KQ_LXGww, leFNoUJmJ9o, 0PW9MWDWLH8, NWdc7PyZNLA, puREqwXzyCI, _H1vcldAsP0, 510KQ_LXGww, 3jtjkXSvuJw, 0oXu0XfXYYE, aKPz583WRpQ, DJXUWLs6FI0, hpapqEeb36k, aKPz583WRpQ, _H1vcldAsP0, hpapqEeb36k, wsXxfgJZ4E4, wppAQ8uZpfQ, DJXUWLs6FI0, F1b5ouja_VI, dgW5kpeSB1A, sECcOTO8Ij4, YInRqgNMLBc, p8XP7A7kvzM, tpyQLIpv4Yk, 3jtjkXSvuJw, sOIBkZsGb0A, p8XP7A7kvzM, puREqwXzyCI, wsXxfgJZ4E4, Z1rZAT2GtmI, oSS6kGWNEeA, Z1rZAT2GtmI, cJ1zhq3yNBM, _H1vcldAsP0, _H1vcldAsP0, p8XP7A7kvzM)), List(comedy, 206, List(j7WlcSwe8Ws, nlodY8nMw-A, Mn-3c6of8t8, z4bLKt9k5dk, aRXgvkpMZrI, BsfhHKx6ajA, 5nEogChRGE8, nlodY8nMw-A, z4bLKt9k5dk, z4bLKt9k5dk, cHB_s970Uyw, 7DLKv39MLbg, _H1vcldAsP0, FHl0nIdbiLA, VsYmwBOYfW8, g5c1bk8weaQ, aRXgvkpMZrI, z4bLKt9k5dk, vIVaLtJmyPs, 3s1rvMFUweQ, 3iXwXYflCSI, 5nEogChRGE8, leFNoUJmJ9o, aRXgvkpMZrI, nlodY8nMw-A, hbmdI8A7SSo, aRXgvkpMZrI, jp9hK-jY6yY, puREqwXzyCI, jp9hK-jY6yY, hpapqEeb36k, g5c1bk8weaQ, Mn-3c6of8t8, vIVaLtJmyPs, mwpHSMv1pI4, nlodY8nMw-A, Z1rZAT2GtmI, nlodY8nMw-A, Z1rZAT2GtmI, o3CaFMmKA7A, hpapqEeb36k, leFNoUJmJ9o, 3iXwXYflCSI, puREqwXzyCI, 3iXwXYflCSI, BsfhHKx6ajA, 5nEogChRGE8, hpapqEeb36k, g5c1bk8weaQ, mwpHSMv1pI4, vIVaLtJmyPs, o3CaFMmKA7A, Mn-3c6of8t8, g5c1bk8weaQ, mwpHSMv1pI4, BsfhHKx6ajA, _H1vcldAsP0, hpapqEeb36k, z4bLKt9k5dk, mwpHSMv1pI4, _H1vcldAsP0, leFNoUJmJ9o, Z1rZAT2GtmI, uT3wso5Zp7k, hpapqEeb36k, vIVaLtJmyPs, hpapqEeb36k, 3s1rvMFUweQ, 3s1rvMFUweQ, aRXgvkpMZrI, jp9hK-jY6yY, hbmdI8A7SSo, g5c1bk8weaQ, vIVaLtJmyPs, 

## Task #4

In [0]:
def top_channels(videos_df):
    """
    Show the top 20 channels by the number of views for the whole period. Note, 
    if there are multiple appearances of the same video for some channel, you should 
    take into account only the last appearance (with the highest number of views).
    """
    # Cast and transform input data.
    channel_videos_df = videos_df.select(
        f.col("channel_title"),
        f.col("video_id"),
        f.to_date(f.from_unixtime(f.unix_timestamp(f.col("trending_date"), "yy.dd.MM"))).alias("date"), 
        f.col("views").cast(t.LongType()).alias("views"), 
    )
    
    # Take only last appearances for each video of a channel.
    window = w.partitionBy("channel_title", "video_id").orderBy(f.col("views").desc())
    channel_videos_once_df = (
        channel_videos_df
            .withColumn("rank", f.row_number().over(window))
            .where(f.col("rank") == 1)
    )
    
    # Get top 20 channels by total number of views for the whole period.
    channel_stats_df = (
        channel_videos_once_df
            .withColumn("video_stats", f.struct(f.col("video_id"), f.col("views")))
            .groupBy("channel_title")
            .agg(
                f.min("date").alias("start_date"),
                f.max("date").alias("end_date"),
                f.sum("views").alias("total_views"),
                f.collect_list("video_stats").alias("video_views")
            )
            .select(
                f.struct(
                    f.col("channel_title"),
                    f.col("start_date"),
                    f.col("end_date"),
                    f.col("total_views"),
                    f.col("video_views")
                ).alias("channel")
            )
            .orderBy(f.col("channel.total_views").desc())
            .limit(20)
    )
    return channel_stats_df

In [0]:
top_channels_df = top_channels(videos_df)
display(top_channels_df)

channel List(Ozuna, 2017-11-17, 2018-06-02, 487997039, List(List(Ck4xHocysLw, 137081637), List(X8sSXU-J8fI, 60426299), List(iNf6VErGDLI, 1677111), List(wfWkmURBNv8, 288811992))) List(NickyJamTV, 2018-04-07, 2018-06-14, 465469058, List(List(V15BYnSr0P8, 20409647), List(_I_D_8Z4sJE, 424538912), List(kFMZUxX6K6o, 20520499))) List(DrakeVEVO, 2018-03-25, 2018-05-13, 364312023, List(List(U9BwWKXjVaI, 106147032), List(xpVfcZ0ZcFM, 258164991))) List(Flow La Movie, 2018-05-18, 2018-05-18, 337621571, List(List(9jI-z9QN6g8, 337621571))) List(Bad Bunny, 2018-03-23, 2018-03-23, 328860380, List(List(kLpH1nSLJSs, 328860380))) List(Ed Sheeran, 2017-11-27, 2018-06-02, 297553382, List(List(2Vv-BfVoq4g, 138578860), List(817P8W8-mGE, 76816483), List(iWZmdoY1aTE, 82158039))) List(ibighit, 2017-11-24, 2018-06-14, 296558059, List(List(2tDKp41nrw8, 8753550), List(7C2z4GqqS5E, 123010920), List(8O_MwlZ2dEg, 15635625), List(D_6QmL6rExk, 12709520), List(OK3GJ0WIQ8s, 23416810), List(ixxR3ZoqnF0, 8484137), List(kTlv5_Bs8aw, 54083634), List(kX0vO4vlJuU, 20721039), List(p8npDG2ulKQ, 29742824))) List(ChildishGambinoVEVO, 2018-06-11, 2018-06-11, 259721696, List(List(VYOjWnS4cMY, 259721696))) List(Marvel Entertainment, 2017-11-29, 2018-06-06, 236205127, List(List(3VbHg5fqBYw, 3111226), List(5iOhzJdDawE, 7595900), List(6ZfuNTqbHE8, 100672931), List(8_rTIAOohas, 8842980), List(HmBIn9De-Yc, 340750), List(KweizHAroUU, 180322), List(PJBmeqpw3DY, 2295021), List(QwievZ1Tx-8, 56293347), List(UUkn-enk2RU, 20667905), List(gbRijjvIeyk, 2224539), List(pVxOVlm_lE8, 33980206))) List(TaylorSwiftVEVO, 2017-11-16, 2018-04-17, 230798552, List(List(MvIwx0JThsk, 4591889), List(V54CEElTF_U, 21893347), List(dfnCAmr569k, 87043012), List(tCXGJQYZ9JA, 117270304))) List(jypentertainment, 2017-12-11, 2018-06-14, 213386790, List(List(2MiQonPvlVM, 2361405), List(A70B_LKyOrU, 5050120), List(MPhAEcLaiNs, 2709257), List(Sy3ERg7OCWo, 2536670), List(Xo8FPXlI3CU, 2091614), List(i0p1bmr0EmE, 98250935), List(lpzJNwur6Zk, 4336590), List(rRzxEiBLQCA, 55754734), List(sS0LCjOiIhc, 31391976), List(zi_6oaQyckM, 8903489))) List(ArianaGrandeVevo, 2018-05-26, 2018-05-26, 208876887, List(List(ffxKSjUwKdU, 208876887))) List(BeckyGVEVO, 2018-05-26, 2018-05-26, 200862743, List(List(zEf423kYfqk, 200862743))) List(Cardi B, 2018-01-09, 2018-06-14, 189436342, List(List(H4Hb6HcCm_E, 14181777), List(U4fErC9skHE, 49603959), List(l3uG4T8pJfw, 6744540), List(sXP6vliZIHI, 24651559), List(xTlNMmZKwpA, 94254507))) List(SebastianYatraVEVO, 2018-02-23, 2018-05-05, 185610141, List(List(WtE011iVx1Q, 92838957), List(sD9_l3oDOag, 92771184))) List(PostMaloneVEVO, 2017-12-06, 2018-04-28, 176803198, List(List(UceaB4D0jpo, 71173287), List(au2n7VVGv_c, 105629911))) List(YouTube Spotlight, 2017-11-22, 2017-12-24, 170800687, List(List(1cgK-BIrXes, 916104), List(FlsCjmMhFmw, 169884583))) List(Daddy Yankee, 2018-02-14, 2018-02-14, 167456025, List(List(sGIm0-dQd8M, 167456025))) List(WORLDSTARHIPHOP, 2017-11-14, 2018-06-14, 161490535, List(List(JvVYL7s-HMc, 846012), List(LJjsm6CVsG8, 53494574), List(MEYmQlWBeAE, 3582721), List(MnK9_fWPT3Y, 2030890), List(TVARgV7H4xw, 992009), List(Vm_CmfA5gRI, 1867270), List(VmwOMtkDxtk, 14008109), List(WZEFya56qPw, 842661), List(aMGQgC5yV-o, 2971860), List(giOZ3EAleeI, 3504679), List(oVruAfu53z4, 662034), List(z5WrgDzNIZ0, 76687716))) List(MigosVEVO, 2017-11-16, 2018-04-24, 161132971, List(List(A_xWDAbnBSU, 14445005), List(HI-mXMr8glQ, 22031899), List(RHUxyXZBXY8, 4083066), List(TbfxmTQkLAE, 17957402), List(fGqdIPer-ms, 100159686), List(hYc95vB-nT4, 2455913)))

## Task #5

In [0]:
def top_trending_channels(videos_df):
    """
    Show the top 10 channels with videos trending for the highest number of days 
    (it doesn't need to be a consecutive period of time) for the whole period.
    In order to calculate it, you may use the results from the question No1.
    The total_trending_days count will be a sum of the numbers of trending days 
    for videos from this channel.
    """
    # Get all trending periods for each video.
    trending_videos_df = top_trending_videos(videos_df)
    
    # Get channel name - video id mapping.
    channel_video_df = videos_df.select("video_id", "channel_title").distinct()
    
    # Add channel name column to trending videos.
    videos_trending_days_df = (
        trending_videos_df.alias("tv")
            .join(channel_video_df.alias("cv"), f.col("tv.video.id") == f.col("cv.video_id"), how="left")
            .select(
                f.col("cv.channel_title").alias("channel_name"),
                f.struct(
                    f.col("tv.video.id").alias("video_id"),
                    f.col("tv.video.title").alias("video_title"),
                    f.size(f.col("tv.video.trendingDays")).alias("trending_days")
                ).alias("video_day")
            )
    )
    
    # Get top 10 channels by the ammount of trending videos.
    top_channels_df = (
        videos_trending_days_df
            .groupBy("channel_name")
            .agg(
                f.sum(f.col("video_day.trending_days")).alias("total_trending_days"),
                f.collect_list(f.col("video_day")).alias("videos_days")
            )
            .select(f.struct(
                f.col("channel_name"),
                f.col("total_trending_days"),
                f.col("videos_days")
            ).alias("channel"))
            .orderBy(f.col("channel.total_trending_days").desc())
            .limit(10)
    )
    return top_channels_df

In [0]:
top_trending_channels_df = top_trending_channels(videos_df)
display(top_trending_channels_df)

channel List(The Tonight Show Starring Jimmy Fallon, 208, List(List(89PKbJ2NAqc, Maroon 5 Busks in NYC Subway in Disguise, 6), List(DHMBJ2do1XU, Arctic Monkeys: Four Out of Five, 4), List(Fh3zmz7Ravw, John Boyega Shows Off His Best Michael Jackson Dance Moves, 6), List(GoNT7uT8oTA, Al Capone Helped Jack White Make Humoresque on Boarding House Reach Album, 4), List(Ox-DSihhpBM, Chloe Kim Photobombs Fans and Finds Out She Made the Cover of Kellogg's Corn Flakes, 5), List(P6K9Y6FWo74, Jimmy Fallon, Camila Cabello and The Roots Sing Havana (Classroom Instruments), 2), List(QsSxRElRe1I, Tag-Team Lip Sync Battle with WWE's Triple H, Stephanie McMahon and The New Day, 6), List(R9YYmoJjBxI, Fast Dance-Off with Jennifer Lopez, 1), List(Rtyv9919Lh0, Kylie Jenner Reveals Her Baby's Name, McDonald's French Fries Cure Baldness - Monologue, 1), List(SDGHRQyZKes, Sam Smith Will Only Do Karaoke to Fifth Harmony, 3), List(VVoePRCvENk, Adam Sandler FaceTimes Justin Bieber While on Vacation, 1), List(gjXrm2Q-te4, Jimmy Fallon Pays Tribute to His Mother Gloria, 8), List(l4HxWVA59zk, St. Vincent: Slow Disco, 1), List(lHNmUUi6LzM, Tina Fey Addresses 30 Rock Reboot Rumors, 4), List(mRo6MnXObuE, Camila Cabello Debuts Never Be the Same, 2), List(nE_TyW-7F4Q, Justin Timberlake on His Super Bowl Halftime Show and Prince Tribute, 4), List(oU651Rj9QP4, Black Panther Stole the Idea from Tracy Morgan's Black Bobcat, 2), List(wLZIWQnACjc, Niall Horan: Too Much to Ask, 3), List(yzJtC835sio, Google Translate Songs with Kelly Clarkson, 3), List(8LPVjHxXvJM, Jimmy Interviews Cardi B, 19), List(KMTJrFPie6w, Jimmy Fallon, Anna Kendrick, Darlene Love & The Roots Sing Christmas (Classroom Instruments), 1), List(QqJZxmU-iZM, James Taylor Sings Fire and Fury (Fire and Rain Parody), 1), List(eYf1IKFNHgM, Panic! At The Disco's Brendon Urie Sings the DuckTales Theme Song, 1), List(hNpgwz8wvE8, Rex Orange County: Loving Is Easy, 1), List(hcCCe_R8e9U, Camila Cabello Almost Kissed Nick Jonas on New Year's Eve, 3), List(P2z7Jwu5OfQ, Rebel Wilson Shares the Secret to Her American Accent, 1), List(WsZXJKfJ52g, Bridget Everett Performs a Karaoke Version of Miley Cyrus' The Climb, 2), List(af6L1jBZGYA, Jimmy Fallon and Paul Rudd Recreate King of Wishful Thinking Music Video, 12), List(4FgV0yBZG6E, Star Wars Whisper Challenge with Daisy Ridley, 2), List(A9R5tJPbcKI, Wheel of Freestyle with Black Panther's Letitia Wright, 1), List(BsjQqm60ZEI, Dance Battle with the Stranger Things Kids, 1), List(VSKuhdmYkUU, Liam Payne and Rita Ora: For You (Fifty Shades Freed), 1), List(ZKg3jKEbgqs, Marshmello & Anne-Marie: Friends, 8), List(ZNsvGhLM42c, One-Second Prince Song Quiz with Questlove, 1), List(d6wJfdfFnYY, Migos: Stir Fry, 6), List(dl7tsRkAD7w, Virtual Reality Pictionary with John Boyega and Bella Thorne, 1), List(g7IfZX91qV0, The Gentlemen's Chorus Sings Green Day's Good Riddance, 1), List(rXqh6AcIb-c, Ariana Grande Spills All the Tea About Her Album Title and Release, 1), List(zbGSbZXzvqw, Cord & Tish (Will Ferrell & Molly Shannon) Preview the Royal Wedding, 25), List(7SAisWFutbw, Dr. Evil Gets Fired from Trump's Cabinet, 2), List(82QbMrg2HoI, David Blaine Sews His Mouth Shut in Insane Trick (w/Jimmy, Priyanka Chopra & The Roots), 5), List(NaY91YjVbEM, Musical Genre Challenge with Ariana Grande, 1), List(PdWe5ULGy_s, Singing Whisper Challenge with Alicia Keys, 5), List(UM_3NQtO9BE, Kali Uchis ft. Tyler, The Creator: After the Storm, 2), List(VZsBRynPXHY, Jaden Smith: Icon, 9), List(XAcjj16GMR4, Rihanna Chased Down Aaron Paul in a Parking Lot, 3), List(XKrV_JqZX1Q, Name That Song Challenge with Blake Shelton, 1), List(kD-_iyS95AQ, History of TV Theme Songs with Will Smith, 11), List(lq0WUudJiSM, Offset & Metro Boomin Perform Ric Flair Drip with the Real Ric Flair, 1), List(m6lY1GXTu5M, Ariana Grande, Jimmy & The Roots Sing No Tears Left to Cry w/ Nintendo Labo Instruments, 6), List(mriYyuDmB58, Zendaya Shows One of Her and Zac Efron's Trapeze Fails for The Greatest Showman, 7))) Lis

## Task #6

In [0]:
def top_category_videos(videos_df, categories_df):
    """
    Show the top 10 videos by the ratio of likes/dislikes for each category
    for the whole period. You should consider only videos with more than 100K views. 
    If the same video occurs multiple times you should take the record when
    the ratio was the highest.
    """
    # Cast and transform input data.
    # Filter out video with less than 100K views.
    # Calculate like/dislike ratio for each video.
    videos_ratio_df = (
        videos_df
            .select(
                f.col("video_id"),
                f.col("title").alias("video_title"),
                f.col("views").cast(t.LongType()).alias("views"),
                f.col("likes").cast(t.LongType()).alias("likes"), 
                f.col("dislikes").cast(t.LongType()).alias("dislikes"), 
                f.col("category_id")
            )
            .where(f.col("views") > 100000)
            .withColumn("ratio_likes_dislikes", f.col("likes") / f.col("dislikes"))
            .select(
                f.col("category_id"),
                f.col("video_id"),
                f.col("video_title"),
                f.col("views"),
                f.col("ratio_likes_dislikes")
            )
    )
    
    # Get the highest liked/disliked ratio for videos that appear more than once.
    video_window = w.partitionBy("video_id").orderBy(f.col("ratio_likes_dislikes").desc())
    ratio_videos_df = (
        videos_ratio_df
            .withColumn("video_rank", f.row_number().over(video_window))
            .where(f.col("video_rank") == 1)
    )

    # Get top 10 videos by ratio for each category.
    category_window =  w.partitionBy("category_id").orderBy(f.col("ratio_likes_dislikes").desc())
    category_ratio_df = (
        ratio_videos_df
            .withColumn("category_rank", f.row_number().over(category_window))
            .where(f.col("category_rank") <= 10)
            .select(
                f.col("category_id"),
                f.struct(
                    f.col("video_id"),
                    f.col("video_title"),
                    f.col("ratio_likes_dislikes"),
                    f.col("views"),
                ).alias("video")
            )
    )

    # Transform data to its final shape.
    # Join with categories DF to get category name.
    top_category_videos_df = (
        category_ratio_df.alias("cr")
            .groupBy("category_id")
            .agg(f.collect_list(f.col("video")).alias("videos"))
            .join(categories_df.alias("c"), f.col("cr.category_id") == f.col("c.id"), how="left")
            .select(f.struct(
                f.col("cr.category_id").alias("category_id"),
                f.col("c.title").alias("category_name"),
                f.col("videos")
            ).alias("category")) 
    )
    return top_category_videos_df

In [0]:
top_category_videos_df = top_category_videos(videos_df, categories_df)
display(top_category_videos_df)

category List(1, Film & Animation, List(List(WkzmaFnPKOs, 81. I'm not good enough., 311.1, 128972), List(4yG_k2Zlw7Y, GOING FISHING. A Stop motion Animation by Guldies, 211.15254237288136, 167196), List(QfmgAmtGXwo, MY FAVOURITE FILMS THIS YEAR 🎬, 208.91549295774647, 100065), List(7FM_MfpYOLU, PEOPLE TELL THEIR CRUSH THEY LIKE THEM (vol. IX), 201.7246376811594, 621594), List(jm_mZqqL40M, 83. You + Me, 172.50632911392404, 112278), List(739XDwYBEdI, Wrestle in Peace, 163.3, 110798), List(caIFNg_JRL4, Robin Williams: Come Inside My Mind (2018) Official Trailer | HBO, 160.78947368421052, 296548), List(uxbQATBAXf8, Deadpool 2 | With Apologies to David Beckham, 147.68104312938817, 4369014), List(YFHHGETsxkE, PAPERS, PLEASE - The Short Film (2018) 4K SUBS, 135.265350877193, 2005280), List(72QQsWm7yFk, Marvel's Biggest Baddie Just Wants To Be Your Daddy (Avengers: Infinity War), 131.625, 102941))) List(10, Music, List(List(v9ea5VDQfXg, JONGHYUN 종현 '우린 봄이 오기 전에 (Before Our Spring)' MV, 940.6694915254237, 1745016), List(c5_LROaHGtw, [EPISODE] BTS (방탄소년단) 'MIC Drop' MV Shooting, 692.3022598870057, 1447420), List(bUMWiiOlee4, [몬채널][S] 몬스타엑스(MONSTA X) - 그놈의 크리스마스 (Lonely Christmas), 676.7971014492754, 331120), List(S1XtMT9ER0o, Little Girl by Christina Grimmie (OFFICIAL VIDEO), 529.2954545454545, 166404), List(ewm0y9nL--Q, bitter content - original song feat. Dom Fera || dodie, 482.38461538461536, 235321), List(STEUAcTmXTg, [MIXTAPE] I.M - Fly With Me (MV), 473.070796460177, 429082), List(o31pGcwUmCM, [SPECIAL VIDEO] NU'EST W(뉴이스트W) & SEVENTEEN(세븐틴) - HEAVEN, 453.81538461538463, 550139), List(-7tSTUR7FG0, NCT U 엔시티 유 'BOSS' Dance Practice, 451.2899408284024, 1092530), List(J41qe-TM1DY, JONGHYUN 종현 '빛이 나 (Shinin’)' MV, 436.0326831839747, 4285299), List(Q48VduIflPk, [STATION] SMTOWN 'Dear My Family (Live Concert Ver.)' MV, 431.90410958904107, 2332110))) List(15, Pets & Animals, List(List(3jtjkXSvuJw, Try Not to Laugh at This Silly Kitten, 240.23333333333332, 101048), List(45tSUnisIos, 5 Signs You Work With Cats, 227.17777777777778, 106298), List(KKwmGuQaMfo, EPIC DIY Gingerbread House for Cats!, 185.76785714285714, 107972), List(SJsvPv5Q_oY, KITTEN and CAT, 171.9718309859155, 424587), List(_4_V7ZGCYDE, Cat with Short Legs Looks Like a Tiny Potato - GISELLE | The Dodo Little But Fierce, 159.61325966850828, 1045263), List(rplCCSqWXIY, Head Over Heels (A Valentines Special) - Simon's Cat | BLACK & WHITE, 135.55414012738854, 404977), List(OPtomB--3Ss, What Cat People Do When It's Cold Outside, 125.92660550458716, 194905), List(fS2fsa1fuIw, If It Fits, I Sits..., 106.71014492753623, 655036), List(DRfniGCgW0I, Cat Alarm Clock, 96.47872340425532, 141076), List(x8DegXNFOns, What's Your Cat's Petting Style?, 92.41666666666667, 142250))) List(17, Sports, List(List(Vm4Xn5vjqRA, CRISTIANO RONALDO E FRED, O GRANDE ENCONTRO, 315.58679446219384, 3990953), List(AB_u_kOSP8Y, Ronaldinho's most jaw-dropping plays with Barça, 202.04, 199610), List(6F5x2ArbQKU, MY MUM TRIED GYMNASTICS! {Wipeout}, 196.14285714285714, 204263), List(JtIY1Naxg0M, Game of Zones - S5E7: NBA 1K, 183.52631578947367, 445567), List(NHrwcQQ38bA, Candide Thovex - quattro 2, 167.93693693693695, 388810), List(wjy9Jgnjv6U, Neil and Blake Push A Fat Bike To Its Limits, 139.11904761904762, 157595), List(58sRIu0PUok, REACTING TO MY OLD GYMNASTICS WITH MY DAD!, 136.2, 202532), List(_9wK8hVvjAU, Lampard Reveals Why England Never Won Anything | FIFA and Chill ft. Poet & Vuj, 132.24193548387098, 156925), List(hU_oxkN9wsw, Keyshia Cole Would F*** Up Nick Cannon's Car | Wild 'N Out | #Wildstyle, 124.6832298136646, 625474), List(zxjv0lo8bU8, MARCELO's son ENZO shows off his skills in the Real Madrid dressing room, 120.22368421052632, 214591))) List(19, Travel & Events, List(List(-trTIbE3N4Y, I LOVE JAPAN, 265.3484848484849, 109154), List(MU29Wqg_BVo, Brazil's Video Game Gray Markets, 143.98648648648648, 120526), List(zmcGIBpgG-Y, Nikuman - Magic Japanese Steam Buns, 133.79518072289156, 182617), List(_6l